# Problem Set 4: Equivalence, Representation, and Intervals

These questions will help (1) strengthen your understanding of what we might mean by equal pitches/notes, (2) get a better sense of how pitches and durations (a) might be represented and (b) are represented in `music21`, and (3) figure out why working with intervals is so hard.

Note -- that there is a property on Note and Pitch objects called `diatonicNoteNum` which you may **not** use in this problem set but you may use it after this problem set, but feel free to learn what it is and why it might be important.

# Question 1: Spaces and Clefs

These questions assume that we're going to be using a standard five-line staff and by convention the lowest line of the staff is called "line 1", the second line from the bottom is "line 2" and so on to line 5.  The space between line 1 and line 2 ("F4" or "F#4" etc. in treble clef) we will call line 1.5.  Ledger lines can also have lines, so lines can have numbers like 0 (for middle C in treble clef) or 6 (for...well...middle C in bass clef) or negative or large positive numbers. 

Given a name of a clef from "treble", "alto", "tenor", "bass" and a `music21` pitch.Pitch object, return the line (or line fraction) the note sits on.  You may need to review "alto" and "tenor" clef if they were not covered in your 21m.301 class.  (Don't forget the doc string...)  

I am temporarily "re-locking" the property on Pitch objects called `diatonicNoteNum`, so do *not* use it in this assignment.

In [ ]:
from music21 import pitch

In [ ]:
def line_from_pitch(clef_str: str, p: pitch.Pitch) -> float:
    pass

For your testing:

In [ ]:
assert line_from_pitch('bass', pitch.Pitch('G2')) == 1.0
assert line_from_pitch('alto', pitch.Pitch('A4')) == 5.5
assert line_from_pitch('tenor', pitch.Pitch('A3')) == 3.0

# Section 2: Intervals

## Question 2a: Chromatic Intervals

Now let is explore the chromatic interval distance (in semitones) between two notes.

(We are going to take up what we did in class and go a bit further.)

First a pretty easy Q.  I've already written the code and some tests.  You document it, including correct type annotations, based on what I use as test code:

In [ ]:
def pitches_to_chromatic(p1: int, p2: int) -> int:
    return p2.ps - p1.ps

In [ ]:
assert pitches_to_chromatic(pitch.Pitch('F3'), pitch.Pitch('B3')) == 6.0
assert pitches_to_chromatic(pitch.Pitch('B3'), pitch.Pitch('F3')) == -6.0

## Question 2b: Pitches to Diatonic

Great, now I'll turn the coding back over to you.

Create a function that, given two music21.pitch.Pitch objects, returns the undirected diatonic interval between the two of them in the form of, for instance, M2 = major second, m3 = minor third, P12 = perfect twelfth.  Use "A" and "d" for Augmented and diminished, and there may be doubly augmented or triply diminished, as "AA" or "ddd", etc.

By undirected diatonic interval, I mean that "C4 -> A5" gives the same interval as "A5 -> C4". 

(Nothing smaller than P1 is allowed because there is a problem with diminished unisons: do they exist and if so, what is their direction? Is the interval from C#4 to C4 a diminished unison? or a descending augmented unison? I prefer the latter, because otherwise, it is hard to say whether a diminished unison is ascending or descending (is it a negative times a negative?)).

In [ ]:
def pitches_to_diatonic_interval(p1: pitch.Pitch, p2: pitch.Pitch) -> str:
    pass

Here are some test cases...

In [ ]:
P = pitch.Pitch
assert pitches_to_diatonic_interval(P('C4'), P('A4')) == 'M6'
assert pitches_to_diatonic_interval(P('A4'), P('C4')) == 'M6'
assert pitches_to_diatonic_interval(P('C4'), P('F4')) == 'P4'
assert pitches_to_diatonic_interval(P('C4'), P('E#4')) == 'A3'
assert pitches_to_diatonic_interval(P('C#2'), P('C-5')) == 'dd22'

# Section 3: Equivalence and OPTIC

For questions 3a-e, You may try to solve these problems using strings or `music21` pitch.Pitch objects instead.  If you do, however, you may not use the `.transpose()` method or the `.diatonicNoteNum` property.  

You may use the following functions which you may have written in a previous PSet, or anything else you have already written for other PSets:

In [ ]:
def pitch_name_to_pitch_class(pitch_name: str) -> int:
    '''
    Given a pitch name with or without octave number, return the pitch class.
    '''
    pitch_defaults = {'C': 0, 'D': 2, 'E': 4, 'F': 5, 'G': 7, 'A': 9, 'B': 11}
    letter_name_alone = pitch_name[0].upper()
    accidentals = pitch_name[1:]
    pitch_class_number = pitch_defaults[letter_name_alone]
    pitch_class_number += accidentals.count('#')
    pitch_class_number -= accidentals.count('-')
    return pitch_class_number % 12

def pitch_name_to_pitch_space(pitch_name: str) -> int:
    """
    Given a pitch name with octave like "C#4" return an integer of the 
    pitch_space (not MIDI) number.
    
    Deals with tricky cases like B#3 mapping to a higher pitch space
    than C-4.
    
    Does not deal with negative octaves.
    """
    import re
    
    num_sharps = pitch_name.count('#')
    num_flats = pitch_name.count('-')
    offset = num_sharps - num_flats
    pitch_name = pitch_name.replace('#', '').replace('-', '')
    octave_match = re.search(r'(\d+)', pitch_name).group(1)
    pitch_name = pitch_name.replace(octave_match, '')
    pitch_class = pitch_name_to_pitch_class(pitch_name)
    return pitch_class + offset + (12 * (int(octave_match) + 1))

## Question 3a: Warmups on Pitch Sets

Read Tymoczko 2.4 and 2.8 before attempting these questions:

One of Dmitri Tymoczko's major contributions to music theory (in my opinion) is his attempt to systematize the types of meanings we have when we say that two chords are "the same" or "equal" or "equivalent" and notes that two people might disagree as to what this means depending on what they are **analyzing** music to search for.  He comes up with five symmetry operations which he abbreviates as "OPTIC".  Students who have taken 21m.310 will know some of these operations.  For the rest of us, some of these will be new; some intuitive, some less so.

For all of the exercises in Question 3, **assume enharmonic equivalence** (S-equality) -- so Bb == A#.  This is why we've given the `pitch_name_to_pitch_class` and `pitch_name_to_pitch_class` activities above.

Let's do some warmup activities.

`pitch_set_0` and `pitch_set_1` are two pitch sets equivalent under the "O" symmetry (but `pitch_set_1` is not ['C4', 'F4']):

In [ ]:
pitch_set_0 = ['C4', 'F4']  # DO NOT CHANGE ME
pitch_set_1 = []  # TODO: fill me in

pitch_set_2 and pitch_set_3 are equivalent under "PT" but not under "P" or "T" alone, and without O, I, or C symmetry.

In [ ]:
pitch_set_2 = ['A4', 'E5', 'C#4']  # DO NOT CHANGE ME
pitch_set_3 = []  # TODO: fill me in

And pitch_set_4 and pitch_set_5 have at least three pitches each and require both "I" and "C" symmetry to be equivalent (with or without "T", "O", or "P" symmetry -- up to you):

In [ ]:
pitch_set_4 = []  # TODO: fill me in
pitch_set_5 = []  # TODO: fill me in

Okay, if you've gotten this far, you're ready for the main parts of this Question.  Worth the majority of the points.

## Question 3b: Programming O or C

Given two pitch sets and a string of symmetry operations (assume that they will be taken from the letters "OPTIC") you will eventually write a function (`equivalent_under_operations`) that returns True or False if the two pitch sets are equivalent under those operations.

This is a difficult problem so break it up into smaller steps.  Think through how various operations will interact with each other and how the function (and sub-functions) will need to be organized before starting to actually program them.

To get full points, your operation does NOT need to run optimally efficiently, but it does need to return answers within a few seconds.

> *Why not require efficiency?*  In this class you'll find that a lot of times, the limit on efficiency has nothing to do with run time, but instead the lack of encoded music, or the lack of programmers who have had the time to work on problems.  Ideally we would be running our programs in the lowest big-O AND lowest real-world run times.  For now, we're not in an ideal world.  That's what makes computational music analysis SO cutting edge!


For your testing, are some example cases from Tymoczko's 2.4.4(b) that should return True under the given oporation.

In [ ]:
o_tests = [['C4', 'E5', 'G4'], ['C4', 'F-4', 'G3']]
p_tests = [['E4', 'G4', 'C4'], ['G4', 'E4', 'C4']]
t_tests = [['D4', 'F#4', 'A4'], ['A4', 'C#5', 'E5']]
i_tests = [['G4', 'E4', 'C4'], ['A-4', 'B4', 'E-5']]  # changed from Tymoczko to make it easier to see
c_tests = [['C4', 'C4', 'E4', 'G4'], ['C4', 'E4', 'F-4', 'G4']]

And some tests that should return False:

In [ ]:
not_o_tests = [['C4', 'E5', 'G4'], ['C4', 'F5', 'G3']]
not_p_tests = [['E4', 'G4', 'C4'], []]
not_t_tests = [['D4', 'F#4', 'A4'], ['D4', 'A4', 'F#4']]
not_i_tests = [['C4', 'D-4', 'E-4', 'G4'], ['C4', 'D-4', 'E4', 'F#4']]  # a very famous "not_I" chord pair
not_c_tests = [['C4', 'E4'], ['C4']]

For the first of our smaller steps, we will write a function that returns True if two sets are equivalent under octave equivalence:

In [ ]:
from typing import List

def equivalent_under_O(
    pitch_set_1: List[str], 
    pitch_set_2: List[str]
) -> bool:
    """
    TODO: describe me and write me.
    """
    return False

Now write a script that returns True if two sets are equivalent except for cardinality differences.  When considering the order of pitches assume that if a chord or pitch set has more than one of the same pitch, then the latter pitches are the ones ignored under cardinality equivalence.  For instance `['C4', 'E4', 'C4']` becomes `['C4', 'E4']` and not `['E4', 'C4']`.

In [ ]:
def equivalent_under_C(
    pitch_set_1: List[str], 
    pitch_set_2: List[str]
) -> bool:
    """
    TODO: describe me and write me.
    """
    return False

## Question 3c: Programming OC

Fantastic, now we are going to write a function that tests if a pitch set is equivalent under OC, which is much more useful than O or C alone.

HINT: the answer is neither `if equivalent_under_O(a, b) or equivalent_under_C(a, b)` nor `if equivalent_under_O(a, b) and equivalent_under_C(a, b)`.

What you will find quickly is that you are going to want to define some "reducers" or functions that create simpler representations of your pitch sets.  For instance since for this assignment we do not care about enharmonic spelling, you'll probably quickly want to get your pitch sets into numbers for comparison.  Then you will be able to simplify your chords to make comparisons possible.

In the following sub problem, I have sketched out some `_private_functions` (beginning with underscores) which might be useful in your work (but they don't work).  You do not need to write them unless they are helpful:

In [ ]:
def _reduce_pitch_set_to_pitch_space_numbers(
    pitch_set: List[str]
) -> List[int]:
    return [0, 0, 0]

def _reduce_pitch_set_numbers_under_O(
    pitch_set_nums: List[int]
) -> List[int]:
    return [0, 0, 0]

def _reduce_pitch_set_numbers_under_C(
    pitch_set_nums: List[int]
) -> List[int]:
    return [0, 0, 0]

Enough with the helpers.  Now write `equivalent_under_OC`.  This is the only function that will be tested for passing:

In [ ]:
def equivalent_under_OC(
    pitch_set_1: List[str], 
    pitch_set_2: List[str]
) -> bool:
    """
    TODO: write and document me.
    """
    return False

Equivalent under OC is an important symmetry discussed in Tymoczko 2.4, since it describes a "tone row" or ordered set of pitch classes.  But "OC" is only one of the six combinations of "OPTIC" that are in common use in musical discourse.  We will create each of the other five.

## Question 3d: P symmetry

Next let's add permutation symmetry into the mix.  But this time think ahead to reducers you will write for permutation and when you plan to call it.  I will give the `_private_function()` for a permutation reducer and then ask you to come up with the pitch-class multiset or OP, and "chord (of pitches)" or PC type, and finally the "chord" or OPC symmetry: 

In [ ]:
def _reduce_pitch_set_numbers_under_P(
    pitch_set_nums: List[int]
) -> List[int]:
    """
    (trust me on the type annotations. 
    it's too early to cast this as a set()...)
    """
    pass

def equivalent_under_OP(pitch_set_1: List[str], 
                        pitch_set_2: List[str]) -> bool:
    """
    TODO, write me
    """
    pass

def equivalent_under_PC(pitch_set_1: List[str], 
                        pitch_set_2: List[str]) -> bool:
    """
    TODO, write me
    """
    pass

def equivalent_under_OPC(pitch_set_1: List[str], 
                         pitch_set_2: List[str]) -> bool:
    """
    TODO, write me
    """
    pass


### Question 3e: OPTC and OPTIC

We might think that with 5 letters in OPTIC and each one being able to be on or off, that we'll need to come up with 32 different definitions of equivalent.  Fortunately, we can dismiss most others since they are either rarely used or not defined well enough for two music theorists to agree upon the right answer.  In particular, `T` and `I` operations without `OPC` are rare.  So we only need to define two other symmetry operations: `OPTC` and the full `OPTIC`.  These are the final parts of the Problem Set:

In [ ]:
def equivalent_under_OPTC(pitch_set_1: List[str], 
                          pitch_set_2: List[str]) -> bool:
    """
    TODO, write me
    """
    pass

def equivalent_under_OPTIC(pitch_set_1: List[str], 
                           pitch_set_2: List[str]) -> bool:
    """
    TODO, write me
    """
    pass


Before turning this in, be sure that your whole notebook runs in order (Kernel -> Restart & Run All).  Good luck!

In [ ]:
# eof